In [14]:
import numpy as np
import pandas as pd
import csv
import json

from mapboxgl.viz import *
from mapboxgl.utils import df_to_geojson, create_radius_stops, scale_between,  df_to_hexbin
from mapboxgl.colors import create_color_stops

In [ ]:
# Jenks natural breaks classification for example.
# Slow version - does not require C bindings
# For fast version, see pip install -e "git+https://github.com/perrygeo/jenks.git#egg=jenks"
import json
from pprint import pprint as pp

def jenks_matrices_init(data, n_classes):
    #fill the matrices with data+1 arrays of n_classes 0s
    lower_class_limits = []
    variance_combinations = []
    for i in range(0, len(data)+1):
        temp1 = []
        temp2 = []
        for j in range(0, n_classes+1):
            temp1.append(0.)
            temp2.append(0.)
        lower_class_limits.append(temp1)
        variance_combinations.append(temp2)

    inf = float('inf')
    for i in range(1, n_classes+1):
        lower_class_limits[1][i] = 1.
        variance_combinations[1][i] = 0.
        for j in range(2, len(data)+1):
            variance_combinations[j][i] = inf

    return lower_class_limits, variance_combinations

def jenks_matrices(data, n_classes):
    lower_class_limits, variance_combinations = jenks_matrices_init(data, n_classes)

    variance = 0.0
    for l in range(2, len(data)+1):
        sum = 0.0
        sum_squares = 0.0
        w = 0.0
        for m in range(1, l+1):
            # `III` originally
            lower_class_limit = l - m + 1
            val = data[lower_class_limit-1]

            # here we're estimating variance for each potential classing
            # of the data, for each potential number of classes. `w`
            # is the number of data points considered so far.
            w += 1

            # increase the current sum and sum-of-squares
            sum += val
            sum_squares += val * val

            # the variance at this point in the sequence is the difference
            # between the sum of squares and the total x 2, over the number
            # of samples.
            variance = sum_squares - (sum * sum) / w

            i4 = lower_class_limit - 1

            if i4 != 0:
                for j in range(2, n_classes+1):
                    if variance_combinations[l][j] >= (variance + variance_combinations[i4][j - 1]):
                        lower_class_limits[l][j] = lower_class_limit
                        variance_combinations[l][j] = variance + variance_combinations[i4][j - 1]

        lower_class_limits[l][1] = 1.
        variance_combinations[l][1] = variance

    return lower_class_limits, variance_combinations

def get_jenks_breaks(data, lower_class_limits, n_classes):
    k = len(data) - 1
    kclass = [0.] * (n_classes+1)
    countNum = n_classes

    kclass[n_classes] = data[len(data) - 1]
    kclass[0] = data[0]

    while countNum > 1:
        elt = int(lower_class_limits[k][countNum] - 2)
        kclass[countNum - 1] = data[elt]
        k = int(lower_class_limits[k][countNum] - 1)
        countNum -= 1

    return kclass

def jenks(data, n_classes):
    if n_classes > len(data): return

    data.sort()

    lower_class_limits, _ = jenks_matrices(data, n_classes)

    return get_jenks_breaks(data, lower_class_limits, n_classes)

In [ ]:
#Question 1
#tree_data = pd.read_csv("ny_trees_50000.csv")
tree_data = pd.read_csv("http://www.cis.umassd.edu/~dkoop/cis602-2017fa/a2/ny_trees_50000.csv")


token = os.getenv('MAPBOX_ACCESS_TOKEN')
#token

#Key value pairs
data = df_to_geojson(tree_data,properties=['tree_id'],lat='latitude', lon= 'longitude')


#Creating Visualization
viz = CircleViz(data, access_token=token, height='400px')

#Generate databreaks and colorstops from colorbrewer
#breaks = jenks(tree_data['tree_id'].tolist(), 8)
#color_stops =  create_color_stops(breaks, colors='Blues')


#viz.color_property= "tree_id"
#viz.color_stops = color_stops
viz.zoom = 8.75
viz.center= (-74.0060, 40.7128)
viz.show()


#Final Result for Question 1 is below

In [11]:
#Question 2
#tree_data2 = pd.read_csv("ny_trees_all.csv")
tree_data2 = pd.read_csv("http://www.cis.umassd.edu/~dkoop/cis602-2017fa/a2/ny_trees_all.csv")

stump = tree_data2[tree_data2['status'] == 'Stump']
#stump

token = os.getenv('MAPBOX_ACCESS_TOKEN')

data = df_to_geojson(stump,properties=['tree_id'],lat='latitude', lon= 'longitude')
#data
viz = CircleViz(data, access_token=token, height='400px')


#breaks = jenks(tree_data2['tree_id'].tolist(), 8)
#color_stops =  create_color_stops(breaks, colors='YlGnBu')
#color_stops

#viz.color_property= "tree_id"
#viz.color_stops= color_stops
viz.zoom = 8.75
viz.center= (-74.0060, 40.72138)
viz.show()



#Final Result for Question 2 is below

In [12]:
#Question 3

#tree_data3 = pd.read_csv("ny_trees_50000.csv")
tree_data3 = pd.read_csv("http://www.cis.umassd.edu/~dkoop/cis602-2017fa/a2/ny_trees_50000.csv")

#tree_data3

species_common = pd.DataFrame(tree_data3, columns = ['tree_id','spc_common'])

species_common = tree_data3['spc_common'].value_counts()
top8_species=species_common.head(8)
top8_species.index

## Here converting the list  of spc_common
spc_com = top8_species.index.tolist()
#spc_com


top8  = tree_data3[tree_data3.spc_common.apply(lambda x : x in top8_species)]
#len(top8)



data_1 = df_to_geojson(top8,properties=['tree_dbh','spc_common'],lat='latitude', lon= 'longitude')
#data

#Creating Visualization
viz = CircleViz(data_1, access_token=token, height='400px')

#Generate databreaks and colorstops from colorbrewer
#breaks = jenks(tree_data3['tree_dbh'].tolist(), 7)
color_stops =  create_color_stops(spc_com, colors='Set1')
#color_stops
viz.color_type = "categorical"
viz.color_property= "spc_common"
viz.color_stops = color_stops
viz.zoom = 8.75
viz.center= (-74.0060, 40.7128)
viz.show()

#Final Result for Question 3 is below

In [13]:
##Question 4

#tree_data4 = pd.read_csv('ny_trees_all.csv')
tree_data4 = pd.read_csv("http://www.cis.umassd.edu/~dkoop/cis602-2017fa/a2/ny_trees_all.csv")

hexbin = df_to_hexbin(tree_data4, lat = "latitude",lon = "longitude",radius = 600)



aggregate = []
aggregate = np.linspace(0,1448,8).round(2)


viz = HexbinViz(hexbin[0], access_token=token, height='400px' )
color_stops = create_color_stops(aggregate, colors='Blues')

viz.color_property = "count"
viz.color_stops = color_stops
viz.center=(-74.0060, 40.6938)
viz.zoom = 8.85

viz.show()


#Final Result for Question 4 is below